Les acteurs ont en moyenne quel âge ? données films et acteurs (champs age, birth year et start year)
***age moyen à date du film

1- Appel des deux tables - trie ordre croissant - reset index et drop colonne en trop pour les deux tables

2- Nettoyage de la base Movies :
         - Conservation uniquement des films titleType = movie
         - Retrait des films isadult
         - Suppresion colonne quine me sont plus utiles
         - Explode genre en plusieurs colonnes

3- Nettoyage de la base Actors :
        - Supprimer les acteurs nés avant 1800 pour alléger la base
        - Explode colonne primaryProfession et conserver actor actress
        - Retirer la colonne deathYear
        - Explode colonne knownForTitles en film 1 film 2 etc....
        
        


3- Joindre les tables et retrier :
    - Supprimer les films plus anciens que 1918
    - Suprimer les lignes ou l'âge de l'acteur n'est pas renseigné
(ce tri n'a pas été fait avant car cela permet de nattoyer la base acteurs/movies en même temps)

4 - Créer une colonne âge acteur dans le film : Date du film - date de naissance (startYear - birthYear)

5 - il me faudra une moyenne de cette colonne pour répondre à la question par année






In [1]:
import pandas as pd
from datetime import datetime
from datetime import timedelta
import numpy as np
import plotly.express as px 
import plotly.graph_objects as go 
import matplotlib.pyplot as plt
import seaborn as sns

## 1- Appel des trois tables - trie - reset index et drop colonne en trop pour les deux tables :
 actors = name.basics
 movies = title.basics
 title = 

## Table Actors

In [2]:
# appel de la table acteurs

actors = pd.read_csv('https://datasets.imdbws.com/name.basics.tsv.gz', sep = '\t', low_memory=False)

In [3]:
# tri des acteurs par date de naissance 
actors.sort_values(by=['birthYear'], inplace=True)

#reset index 
actors.reset_index(inplace=True)

#drop colonne index en double 
actors.drop('index',axis = 1, inplace=True)


## Table Movies

In [4]:
# appel de la table films (j'ai pris title basics qui contient l'année du film)

movies = pd.read_csv('https://datasets.imdbws.com/title.basics.tsv.gz', sep = '\t', low_memory=False)
movies.sort_values('startYear', inplace=True)

In [5]:
#reset index base movies
movies.reset_index(inplace=True)

#drop colonne index en double 
movies.drop('index',axis = 1, inplace=True)

## Table Title

In [6]:
# appel de la table title
title = pd.read_csv("https://datasets.imdbws.com/title.principals.tsv.gz", sep="\t", low_memory=False)

In [7]:
# filtre par category actor and actress
title = title.loc[(title['category']=='actor')|(title['category']=='actress')]

In [8]:
#reset index base title
title.reset_index(inplace=True)

#drop colonne index en double 
title.drop('index',axis = 1, inplace=True)

In [9]:
# remplacer les \n par des nan
title.replace('\\N', np.nan, inplace=True)

## 2-Nettoyage de la base Movies :
###          - Remplacer les \N par des nan
###          - Conservation uniquement des films titleType = movie
###          - Retrait des films isadult
###          - Suppresion des colonnes qui ne me sont plus utiles
###          - suppression des lignes aux données startYear et runtimeMinutes avec des nan
###          - change str en int sur les colonnes startYear et runtimeMinutes et tri sur durée + reset index
###          - Tri des valeurs par nconst + set index

In [10]:
# Remplacer les \N par des nan

movies.replace('\\N', np.nan, inplace=True)

In [11]:
#Conservation uniquement des films titleType = movie

movies = movies[movies['titleType'] == 'movie']

In [12]:
# Retrait des films isadult 

movies = movies[movies['isAdult'] == '0']

In [13]:
# supression des colonnes inutiles
movies = movies.drop(columns=['primaryTitle','titleType', 'endYear', 'isAdult'])

#movies = movies.drop(columns=['primaryTitle','originalTitle','titleType', 'endYear', 'isAdult', 'genres'])

In [14]:
# suppression des lignes aux données startYear et runtimeMinutes avec des nan

movies.dropna(subset=['startYear', 'runtimeMinutes' ], inplace=True)

In [15]:
# change str en int sur les colonnes startYear et runtimeMinutes
movies = movies.astype({'startYear': int})
movies = movies.astype({'runtimeMinutes': int})

In [16]:
#je ne conserve que les durées entre 58mn et inf à 270mn
movies = movies[(movies['runtimeMinutes']>=58) & (movies['runtimeMinutes']<=270)]

In [17]:
#reset index base movies (again !)
movies.reset_index(inplace=True)

#drop colonne index en double 
movies.drop('index',axis = 1, inplace=True)

In [18]:
# trie par valeur nconst
movies = movies.sort_values('tconst')

#set_index = nconst
movies = movies.set_index('tconst')

## 3- Nettoyage de la base Actors :
###        - Remplacer les \N par des nan
###        - Supprimer les lignes qui contiennent des nan dans la colonne birthYear  
###        - Retirer les colonnes qui ne me sont pas utiles
###        - Supprimer les acteurs nés avant 1800 + reset index
###        - change str en int sur les colonnes startYear et runtimeMinutes
###        - Tri des valeurs par nconst + set index

In [19]:
# remplacer les \N pas des nan 

actors.replace('\\N', np.nan, inplace=True)

In [20]:
# suppression des lignes qui comportent des Nan dans la colonne birthYear

actors.dropna(subset=['birthYear'], inplace=True)

In [21]:
# Retirer les colonnes qui ne me sont pas utiles
#actors.drop(columns=['deathYear', 'primaryProfession', 'knownForTitles'], inplace=True)

In [22]:
# ne conserve que les rows des acteurs/actrices nés avant 1800
actors = actors[actors['birthYear'] >= '1800']

#reset index base actors (again !)
actors.reset_index(inplace=True)

#drop colonne index en double (again !)
actors.drop('index',axis = 1, inplace=True)

In [23]:
# change str en int sur les colonnes startYear et runtimeMinutes
actors = actors.astype({'birthYear': int})

In [24]:
# Table actors - trie par valeur nconst
actors = actors.sort_values('nconst')

#set_index = nconst
actors = actors.set_index('nconst')

In [25]:
actors.info()

<class 'pandas.core.frame.DataFrame'>
Index: 536885 entries, nm0000001 to nm9993675
Data columns (total 5 columns):
 #   Column             Non-Null Count   Dtype 
---  ------             --------------   ----- 
 0   primaryName        536885 non-null  object
 1   birthYear          536885 non-null  int32 
 2   deathYear          183624 non-null  object
 3   primaryProfession  470302 non-null  object
 4   knownForTitles     523916 non-null  object
dtypes: int32(1), object(4)
memory usage: 22.5+ MB


In [26]:
# check index
actors.head()

primaryName  birthYear deathYear  \
nconst                                            
nm0000001     Fred Astaire       1899      1987   
nm0000002    Lauren Bacall       1924      2014   
nm0000003  Brigitte Bardot       1934       NaN   
nm0000004     John Belushi       1949      1982   
nm0000005   Ingmar Bergman       1918      2007   

                             primaryProfession  \
nconst                                           
nm0000001       soundtrack,actor,miscellaneous   
nm0000002                   actress,soundtrack   
nm0000003  actress,soundtrack,music_department   
nm0000004              actor,soundtrack,writer   
nm0000005                writer,director,actor   

                                    knownForTitles  
nconst                                              
nm0000001  tt0050419,tt0072308,tt0031983,tt0053137  
nm0000002  tt0117057,tt0037382,tt0038355,tt0071877  
nm0000003  tt0054452,tt0049189,tt0056404,tt0057345  
nm0000004  tt0080455,tt0078723,tt0072562,tt0077975  
nm0000005  tt0060827,tt0083922,tt0050986,tt0050976

In [27]:
# explode colonne primaryProfession
#actors[['firstProfession', 'secondProfession', 'thirdProfession']] = actors['primaryProfession'].str.split(',', n=2, expand=True)

#drop colonne primaryProfession
#actors.drop(columns=['primaryProfession'],axis = 1, inplace=True)

In [28]:
# check dataframe actors
#actors.head()

In [29]:
# Je ne garde que les acteurs/actrices de mes trois colonnes : firstProfession, secondProfession, thirdProfession

#actors = actors[(actors['firstProfession'].isin(['actress','actor'])) | ( actors['secondProfession'].isin(['actress','actor'])) | ( actors['thirdProfession'].isin(['actress','actor']))]

In [30]:
#drop colums firstProfession, secondProfession, thirdProfession qui ne me sont plus utiles
#actors.drop(columns=['firstProfession','secondProfession', 'thirdProfession'],axis = 1, inplace=True)

## 3- Nettoyage de la base Title :
###        - Remplacer les \N par des nan
###        - dropna sur les cellules tconst non renseignées
###        - supprimer les colonnes inutiles
###        - Tri des valeurs par nconst + set index

In [31]:
# Remplacer les \N par des nan

title.replace('\\N', np.nan, inplace=True)

In [32]:
#dropna sur les cellules startyear non renseignées

title.dropna(subset=['tconst'],inplace=True)

In [33]:
title.head(2)

tconst  ordering     nconst category  job      characters
0  tt0000005         1  nm0443482    actor  NaN  ["Blacksmith"]
1  tt0000005         2  nm0653042    actor  NaN   ["Assistant"]

In [ ]:
title['job'].value_counts()

In [34]:
# suppression des colonnes inutiles

title.drop(columns=['ordering','job', 'characters'], inplace=True)

In [35]:
# trie par valeur nconst
title = title.sort_values('nconst')

#set_index = nconst
title = title.set_index('nconst')

In [36]:
title.head()

tconst category
nconst                       
nm0000001  tt0055307    actor
nm0000001  tt0031983    actor
nm0000001  tt0029971    actor
nm0000001  tt0507706    actor
nm0000001  tt0038370    actor

## 3- Joindre les tables et retrier :

In [37]:
# Table actors
actors.head(2)


primaryName  birthYear deathYear               primaryProfession  \
nconst                                                                          
nm0000001   Fred Astaire       1899      1987  soundtrack,actor,miscellaneous   
nm0000002  Lauren Bacall       1924      2014              actress,soundtrack   

                                    knownForTitles  
nconst                                              
nm0000001  tt0050419,tt0072308,tt0031983,tt0053137  
nm0000002  tt0117057,tt0037382,tt0038355,tt0071877

In [38]:
# table title:
title.head(2)

tconst category
nconst                       
nm0000001  tt0055307    actor
nm0000001  tt0031983    actor

In [39]:
# merge des tables actors et title 
df_actors_title = actors.merge(title , how='inner', on='nconst')

#reset index de la nouvelle table : df_actors_title
df_actors_title = df_actors_title.reset_index()

#check
df_actors_title.head(2)

nconst   primaryName  birthYear deathYear  \
0  nm0000001  Fred Astaire       1899      1987   
1  nm0000001  Fred Astaire       1899      1987   

                primaryProfession                           knownForTitles  \
0  soundtrack,actor,miscellaneous  tt0050419,tt0072308,tt0031983,tt0053137   
1  soundtrack,actor,miscellaneous  tt0050419,tt0072308,tt0031983,tt0053137   

      tconst category  
0  tt0055307    actor  
1  tt0031983    actor

In [40]:
#set index de la table merge avec la colonne tconst (pour mon prochain merge)
df_actors_title = df_actors_title.set_index('tconst')

#check
df_actors_title.head(2)

nconst   primaryName  birthYear deathYear  \
tconst                                                    
tt0055307  nm0000001  Fred Astaire       1899      1987   
tt0031983  nm0000001  Fred Astaire       1899      1987   

                        primaryProfession  \
tconst                                      
tt0055307  soundtrack,actor,miscellaneous   
tt0031983  soundtrack,actor,miscellaneous   

                                    knownForTitles category  
tconst                                                       
tt0055307  tt0050419,tt0072308,tt0031983,tt0053137    actor  
tt0031983  tt0050419,tt0072308,tt0031983,tt0053137    actor

In [41]:
# merge des tables df_actors_title  et movies

actors_title_movies = df_actors_title.merge(movies, how='inner', on='tconst' )

# check merge actors_title  et movies
actors_title_movies.head(2)


nconst      primaryName  birthYear deathYear  \
tconst                                                       
tt0055307  nm0000001     Fred Astaire       1899      1987   
tt0055307  nm0001666  Debbie Reynolds       1932      2016   

                        primaryProfession  \
tconst                                      
tt0055307  soundtrack,actor,miscellaneous   
tt0055307       actress,soundtrack,writer   

                                    knownForTitles category  \
tconst                                                        
tt0055307  tt0050419,tt0072308,tt0031983,tt0053137    actor   
tt0055307  tt0045152,tt0119360,tt0051051,tt0058708  actress   

                         originalTitle  startYear  runtimeMinutes  genres  
tconst                                                                     
tt0055307  The Pleasure of His Company       1961             115  Comedy  
tt0055307  The Pleasure of His Company       1961             115  Comedy

## Création colonne de l'âge de l'acteur au moment du film

In [42]:
# age_actor_actress = startYear - birthYear
actors_title_movies['age_actor_actress'] = actors_title_movies['startYear'] - actors_title_movies['birthYear']

#check
actors_title_movies.head(2)

nconst      primaryName  birthYear deathYear  \
tconst                                                       
tt0055307  nm0000001     Fred Astaire       1899      1987   
tt0055307  nm0001666  Debbie Reynolds       1932      2016   

                        primaryProfession  \
tconst                                      
tt0055307  soundtrack,actor,miscellaneous   
tt0055307       actress,soundtrack,writer   

                                    knownForTitles category  \
tconst                                                        
tt0055307  tt0050419,tt0072308,tt0031983,tt0053137    actor   
tt0055307  tt0045152,tt0119360,tt0051051,tt0058708  actress   

                         originalTitle  startYear  runtimeMinutes  genres  \
tconst                                                                      
tt0055307  The Pleasure of His Company       1961             115  Comedy   
tt0055307  The Pleasure of His Company       1961             115  Comedy   

           age_actor_actress  
tconst                        
tt0055307                 62  
tt0055307                 29

## Clean df merge comprenant les 3 tables : actors_title_movies

In [43]:
#reset index de la table pour que la Pk soit unique
actors_title_movies = actors_title_movies.reset_index()

#drop colonnes qui m'ont servi uniquement à vérifier mes merges
actors_title_movies.drop(columns=['tconst', 'nconst', 'primaryProfession','knownForTitles','runtimeMinutes', 'genres'], inplace=True)

# je tri ici car cela permet de trier toutes les tables d'un seul et éviter de faire 3 fois la même opé
actors_title_movies = actors_title_movies[(actors_title_movies['startYear'] >= 1918) & (actors_title_movies['startYear'] <= 2021)]

#check
actors_title_movies.head()

primaryName  birthYear deathYear category  \
0     Fred Astaire       1899      1987    actor   
1  Debbie Reynolds       1932      2016  actress   
2       Tab Hunter       1931      2018    actor   
3     Lilli Palmer       1914      1986  actress   
4     Fred Astaire       1899      1987    actor   

                          originalTitle  startYear  age_actor_actress  
0           The Pleasure of His Company       1961                 62  
1           The Pleasure of His Company       1961                 29  
2           The Pleasure of His Company       1961                 30  
3           The Pleasure of His Company       1961                 47  
4  The Story of Vernon and Irene Castle       1939                 40

In [ ]:
#Haunted Transylvania 2

actors_title_movies['originalTitle'] = actors_title_movies['originalTitle']

## Groupby startYear et moyenne des ages des acteurs (tous genres confondus)
### Pour avoir l'âge moyen des acteurs par année

In [53]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_year = round(actors_title_movies.groupby(by=["startYear"]).mean('age_actor_actress'),2)

#reset index
age_mean_year = age_mean_year.reset_index()

#drop colonnes
age_mean_year.drop(columns=['birthYear'], inplace =True)

#rename nom colonne age_actor_actress
age_mean_year.rename(columns={'age_actor_actress':'mean_age_actors_actress'}, inplace=True)

#check df age_mean_year
age_mean_year.head()

startYear  mean_age_actors_actress
0       1918                    36.56
1       1919                    36.48
2       1920                    36.91
3       1921                    37.18
4       1922                    37.29

## Table actor et table actress

In [54]:
# Actors
actors = actors_title_movies[actors_title_movies['category'] == "actor"]

#Actress
actress = actors_title_movies[actors_title_movies['category'] == "actress"]


## Groupby startYear et moyenne des ages des acteurs masculins

In [56]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_year_actors = round(actors.groupby(by=["startYear"]).mean('age_actor_actress'),2)

#reset index
age_mean_year_actors = age_mean_year_actors.reset_index()

#drop colonnes
age_mean_year_actors.drop(columns=['birthYear'], inplace =True)

#rename nom colonne age_actor_actress
age_mean_year_actors.rename(columns={'age_actor_actress':'mean_age_actors'}, inplace=True)

#check df age_mean_year_actors
age_mean_year_actors.head()

startYear  mean_age_actors
0       1918            39.71
1       1919            39.95
2       1920            40.11
3       1921            39.74
4       1922            40.31

## Groupby startYear et moyenne des ages des actrices

In [57]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_year_actress = round(actress.groupby(by=["startYear"]).mean('age_actor_actress'),2)

#reset index
age_mean_year_actress = age_mean_year_actress.reset_index()

#drop colonnes
age_mean_year_actress.drop(columns=['birthYear'], inplace =True)

#rename nom colonne age_actor_actress
age_mean_year_actress.rename(columns={'age_actor_actress':'mean_age_actress'}, inplace=True)

#check df age_mean_year_actress
age_mean_year_actress.head()

startYear  mean_age_actress
0       1918             31.30
1       1919             30.30
2       1920             30.76
3       1921             32.94
4       1922             31.97

## Creation df pour le graph

In [58]:
df_graph = age_mean_year.copy()
df_graph['mean_age_actress'] = age_mean_year_actress['mean_age_actress']
df_graph['mean_age_actors'] = age_mean_year_actors['mean_age_actors']
df_graph.head()

startYear  mean_age_actors_actress  mean_age_actress  mean_age_actors
0       1918                    36.56             31.30            39.71
1       1919                    36.48             30.30            39.95
2       1920                    36.91             30.76            40.11
3       1921                    37.18             32.94            39.74
4       1922                    37.29             31.97            40.31

## Le graph

In [90]:
fig = go.Figure() 

# mean actor and actress together per year
fig.add_trace(go.Scatter(x=df_graph.startYear, 
                    y=df_graph.mean_age_actors_actress, 
                    name="Actors and actress together",
                    line_shape='spline',
                    line_color='green'))

# mean only actress per year
fig.add_trace(go.Scatter(x=df_graph.startYear, 
                    y=df_graph.mean_age_actress,
                    name="Actress",
                    line_shape='spline',
                    line_color='rgb(231,107,243)'))

# mean only actor per year
fig.add_trace(go.Scatter(x=df_graph.startYear, 
                    y=df_graph.mean_age_actors,
                    name="Actors",
                    line_shape='spline',
                    line_color='blue'))


fig.update_layout(title ='<b>Mean age actors and actress since 1918<b>',
                    title_x = 0.5,
                    
                    width=1300,
                    height=600,
                    legend_title="Gender",
                    template='plotly_dark',
                    font_size=13
                    )

fig.show()

## Groupeby originalTitle et moyenne des ages des acteurs (tous genres confondus)
## Ensuite Groupeby startYear et moyenne des ages des acteurs (tous genres confondus)
(Si on ne procède pas ainsi nous n'avons plus les titres des films)

In [68]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_per_film = round(actors_title_movies.groupby(by=["originalTitle"]).mean('age_actor_actress'),2)

#reset index
age_mean_per_film = age_mean_per_film.reset_index()
age_mean_per_film.drop(columns=['birthYear'], inplace =True)

# Retrait des # en début de titre de films
age_mean_per_film['originalTitle'] = age_mean_per_film['originalTitle'].str.lstrip("#")

#check
age_mean_per_film.head()


originalTitle  startYear  age_actor_actress
0                   1 Serial Killer     2013.0              31.00
1              73, Shaanthi Nivaasa     2007.0              44.67
2                    BerhentiDiKamu     2021.0              69.00
3  Bitch, les filles et la violence     2015.0              50.00
4                         BlackSkin     2021.0              49.00

## Idem pour les acteurs et actrices isolées

In [69]:
# Actors
actors = actors_title_movies[actors_title_movies['category'] == "actor"]

# Actress
actress = actors_title_movies[actors_title_movies['category'] == "actress"]

### Acteurs masculins

In [75]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_actor_per_film = round(actors.groupby(by=["originalTitle"]).mean('age_actor_actress'),2)

#reset index
age_mean_actor_per_film = age_mean_actor_per_film.reset_index()
age_mean_actor_per_film.drop(columns=['birthYear'], inplace =True)

#rename nom colonne age_actor_actor
age_mean_actor_per_film.rename(columns={'age_actor_actress':'mean_age_actor'}, inplace=True)

# Retrait des # en début de titre de films
age_mean_actor_per_film['originalTitle'] = age_mean_actor_per_film['originalTitle'].str.lstrip("#")

#check
age_mean_actor_per_film.head()

originalTitle  startYear  mean_age_actor
0               73, Shaanthi Nivaasa     2007.0            53.5
1                     BerhentiDiKamu     2021.0            69.0
2   Bitch, les filles et la violence     2015.0            50.0
3              Ewankosau saranghaeyo     2015.0            16.0
4  Gadhvi (He thought he was Gandhi)     2019.0            34.0

### Acteurs féminins

In [74]:
# calcul moyenne age groupby(by=["originalTitle" & "startYear"])
age_mean_actress_per_film = round(actress.groupby(by=["originalTitle"]).mean('age_actor_actress'),2)

#reset index
age_mean_actress_per_film = age_mean_actress_per_film.reset_index()
age_mean_actress_per_film.drop(columns=['birthYear'], inplace =True)

#rename nom colonne age_actor_actress
age_mean_actress_per_film.rename(columns={'age_actor_actress':'mean_age_actress'}, inplace=True)

# Retrait des # en début de titre de films
age_mean_actress_per_film['originalTitle'] = age_mean_actress_per_film['originalTitle'].str.lstrip("#")

#check
age_mean_actress_per_film.head()

originalTitle  startYear  mean_age_actress
0        1 Serial Killer     2013.0              31.0
1   73, Shaanthi Nivaasa     2007.0              27.0
2              BlackSkin     2021.0              49.0
3     DigitalLivesMatter     2016.0              41.0
4  Ewankosau saranghaeyo     2015.0              32.0

## Creation du df pour le graph mean/movie

In [110]:
df_graph_mean_movie = age_mean_per_film.copy()

df_graph_mean_movie['mean_age_actress'] = age_mean_actress_per_film['mean_age_actress']

df_graph_mean_movie['mean_age_actors'] = age_mean_actor_per_film['mean_age_actor']

df_graph_mean_movie = df_graph_mean_movie[(df_graph_mean_movie['startYear'] >= 2000) & (df_graph_mean_movie['startYear'] <= 2021)]

df_graph_mean_movie = df_graph_mean_movie.astype({'startYear': int})


df_graph_mean_movie.head()

originalTitle  startYear  age_actor_actress  \
0                   1 Serial Killer       2013              31.00   
1              73, Shaanthi Nivaasa       2007              44.67   
2                    BerhentiDiKamu       2021              69.00   
3  Bitch, les filles et la violence       2015              50.00   
4                         BlackSkin       2021              49.00   

   mean_age_actress  mean_age_actors  
0              31.0             53.5  
1              27.0             69.0  
2              49.0             50.0  
3              41.0             16.0  
4              32.0             34.0

In [111]:
df_graph_mean_movie2 = df_graph_mean_movie.sort_values('age_actor_actress', ascending=False)
df_graph_mean_movie2.head(15)

originalTitle  startYear  age_actor_actress  \
66117                  Haunted Transylvania 2       2018              148.0   
132230                         Planet of Doom       2004              148.0   
140010                  Revolutionens kvinnor       2006              134.0   
94510   La tragica fine di Caligula imperator       2017              131.0   
188749                                   Vito       2011              129.0   
60941                       Give Me the Banjo       2011              128.0   
24426                               Byrd 1933       2015              127.0   
16954                         Bartóks Requiem       2008              127.0   
2250              A Boatload of Wild Irishmen       2010              126.0   
57194                              Frivolinas       2014              123.0   
66809                   Heimat lebenslänglich       2005              116.0   
177262                 This Is... Jack Carson       2020              110.0   
156063                  Stalin vspomnil o vas       2009              109.0   
164165                The Bitch of Buchenwald       2010              108.5   
182382                        Twinkle Dammit!       2020              108.0   

        mean_age_actress  mean_age_actors  
66117              28.00            31.50  
132230             23.00            50.67  
140010             53.00            38.67  
94510              66.50            58.00  
188749               NaN              NaN  
60941              29.00            31.33  
24426              26.25            41.00  
16954              33.67            46.00  
2250               24.00            28.00  
57194              36.00            32.50  
66809              30.00            26.00  
177262               NaN            28.00  
156063               NaN            32.25  
164165               NaN            46.67  
182382               NaN              NaN

In [106]:
df_graph_mean_movie.shape

(83310, 5)

## Le graph

In [ ]:
sns.scatterplot(data = df_graph_mean_movie, x = 'originalTitle', y = "age_actor_actress", color='green', label='Together')
#sns.scatterplot(data = df_graph_mean_movie, x = 'originalTitle', y = "mean_age_actress", color='pink', label='Actress')

sns.set(rc = {'figure.figsize':(10,6)})

plt.ylabel('Ages')

plt.title('Mean age per film')

plt.legend(title= 'Gender',loc = "upper left")      

plt.show()

In [109]:
fig = px.scatter(df_graph_mean_movie, 
    x='startYear', 
    y='age_actor_actress',     
    template='plotly_dark',
    hover_name='originalTitle'
)


fig.update_layout(width=1300, height=1000)

fig.show()

## Test du code calcul de la moyenne

In [ ]:
#film Easter Parade pour checker ensuite la moyenne manuellement
check_film = actors_title_movies[actors_title_movies['originalTitle'] == "Easter Parade"]
check_film

#Contrôle manuel = (49 + 26 + 25 + 25) /4 = 31

index    primaryName  birthYear deathYear category  originalTitle  \
122    122   Fred Astaire       1899      1987    actor  Easter Parade   
123    123   Judy Garland       1922      1969  actress  Easter Parade   
124    124  Peter Lawford       1923      1984    actor  Easter Parade   
125    125     Ann Miller       1923      2004  actress  Easter Parade   

     startYear  age_actor_actress  
122       1948                 49  
123       1948                 26  
124       1948                 25  
125       1948                 25

In [ ]:
# selection du film : Easter Parade	et voir si la moyenne age_actor_actress est la même que ci-dessus

age_mean_film_Easter = age_mean2[age_mean2['originalTitle'] == "Easter Parade"]
age_mean_film_Easter

originalTitle  startYear  age_actor_actress
45948  Easter Parade     1948.0               31.0

In [112]:
#Haunted Transylvania 2

actors_title_movies[actors_title_movies['originalTitle'] == 'Haunted Transylvania 2']

primaryName  birthYear deathYear category           originalTitle  \
486719  Alfred Hill       1870      1960    actor  Haunted Transylvania 2   

        startYear  age_actor_actress  
486719       2018                148